# Set up imports

In [1]:
# setting up our imports
import re, string, unicodedata
import numpy as np
import pandas as pd
from pprint import pprint
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = stopwords.words('english')

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel
from gensim.models import LdaModel, LdaMulticore
import gensim.downloader as api
from gensim.models import LsiModel
from gensim.models import ldaseqmodel
from gensim.corpora import Dictionary, bleicorpus
from gensim.matutils import hellinger

nltk.download('wordnet')
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
#from bs4 import BeautifulSoup
#from nltk import word_tokenize, sent_tokenize

# Plotting tools 
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import matplotlib.pyplot as plt
# %matplotlib inline

# Enable logging for gensim - optional
#import logging
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.ERROR)
#logging.root.setLevel(level=logging.INFO)
#import warnings
#warnings.filterwarnings("ignore",category=DeprecationWarning)

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Kornelius\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


# load dataset

In [2]:
# Load dataset
df = pd.read_csv('C:/Users/Kornelius/Desktop/Data 2/nips-papers/papers.csv', header = 0, sep = ';', error_bad_lines=False)
# Drop the columns not needed
df = df.drop(columns=['id', 'event_type', 'pdf_name'], axis=1)

In [3]:
# Drop a row by condition
df = df[df.abstract != 'Abstract Missing']

In [4]:
# sort by year
df = df.sort_values(by=['year'])
df

year                                              title  \
6389  1997        A Neural Network Based Head Tracking System   
5909  1997  Learning Generative Models with the Up Propaga...   
4884  2000   Algorithms for Non-negative Matrix Factorization   
5281  2001  Characterizing Neural Gain Control using Spike...   
4471  2007  Learning Horizontal Connections in a Sparse Co...   
4477  2007                 Predictive Matrix-Variate t Models   
4480  2007                        Competition Adds Complexity   
6095  2007  Progressive mixture rules are deviation subopt...   
6085  2007  Adaptive Embedded Subgraph Algorithms using Wa...   
3564  2007  Estimating disparity with confidence from ener...   
3430  2007          Discriminative Batch Mode Active Learning   
6000  2007   Random Sampling of States in Dynamic Programming   
4515  2007        Mining Internet-Scale Software Repositories   
3434  2007                Computing Robust Counter-Strategies   
5958  2007           The Infinite Gamma-Poisson Feature Model   
4607  2007  Linear programming analysis of loopy belief pr...   
6031  2007  Fitted Q-iteration in continuous action-space ...   
6202  2007  Efficient Convex Relaxation for Transductive S...   
4439  2007  An online Hebbian learning rule that performs ...   
4385  2007  On Ranking in Survival Analysis: Bounds on the...   
6255  2007  The Noisy-Logical Distribution and its Applica...   
4363  2007  Support Vector Machine Classification with Ind...   
3565  2007  Modelling motion primitives and their timing i...   
6271  2007  Modeling image patches with a directed hierarc...   
4276  2007  Gaussian Process Models for Link Analysis and ...   
4226  2007                Spatial Latent Dirichlet Allocation   
6405  2007  Regulator Discovery from Gene Expression Time ...   
6479  2007                            Supervised Topic Models   
3578  2007  EEG-Based Brain-Computer Interaction: Improved...   
6549  2007  A General Boosting Method and its Application ...   
...    ...                                                ...   
5371  2017         Independence clustering (without a matrix)   
5370  2017  Interpretable and Globally Optimal Prediction ...   
5383  2017  From Parity to Preference-based Notions of Fai...   
5368  2017  On Tensor Train Rank Minimization : Statistica...   
5358  2017  Gradients of Generative Models for Improved Di...   
5357  2017  Dual-Agent GANs for Photorealistic and Identit...   
5351  2017  Query Complexity of Clustering with Side Infor...   
3484  2017                       Welfare Guarantees from Data   
5337  2017  Subset Selection and Summarization in Sequenti...   
5327  2017  Clustering Billions of Reads for DNA Data Storage   
5360  2017  Expectation Propagation with Stochastic Kineti...   
5521  2017     Model evidence from nonequilibrium simulations   
5401  2017                Collecting Telemetry Data Privately   
5421  2017  Learning Combinatorial Optimization Algorithms...   
5506  2017  k-Support and Ordered Weighted Sparsity for Ov...   
5501  2017     From Bayesian Sparsity to Gated Recurrent Nets   
5498  2017  Minimax Estimation of Bandable Precision Matrices   
5492  2017  Lower bounds on the robustness to adversarial ...   
5488  2017  Union of Intersections (UoI) for Interpretable...   
5484  2017  Uprooting and Rerooting Higher-Order Graphical...   
5411  2017  When Cyclic Coordinate Descent Outperforms Ran...   
5465  2017  InfoGAIL: Interpretable Imitation Learning fro...   
5450  2017  The Expressive Power of Neural Networks: A Vie...   
5446  2017       Improving the Expected Improvement Algorithm   
5444  2017  Clustering Stable Instances of Euclidean k-means.   
5440  2017  Deliberation Networks: Sequence Generation Bey...   
5436  2017  On the Model Shrinkage Effect of Gamma Process...   
5434  2017      Regret Analysis for Continuous Dueling Bandit   
5459  2017  Identification of Gaussian Process State Space...   
5278  2017                    Hierarchica

In [5]:
df.year.value_counts()

2017    679
2016    569
2014    411
2015    403
2013    360
2012    342
2011    290
2010    288
2009    257
2008    222
2007     99
1997      2
2001      1
2000      1
Name: year, dtype: int64

In [6]:
data = df.abstract.values.tolist()

In [7]:
from nltk.corpus import stopwords 
from nltk.stem.wordnet import WordNetLemmatizer
import string
stop = set(stopwords.words('english'))
exclude = set(string.punctuation) 
lemma = WordNetLemmatizer()
def clean(data):
    stop_free = " ".join([i for i in data.lower().split() if i not in stop])
    punc_free = ''.join(ch for ch in stop_free if ch not in exclude)
    normalized = " ".join(lemma.lemmatize(word) for word in punc_free.split())
    return normalized

data = [clean(data).split() for data in data]  

In [8]:
# remove characters and numbers
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

data_words = list(sent_to_words(data))

In [9]:
data = data_words
# Create Dictionary
id2word = corpora.Dictionary(data)
print((id2word))

Dictionary(16129 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [10]:
# filter words that occur in more than 90% of documents
id2word.filter_extremes(no_above = 0.900)
print(id2word)

Dictionary(4415 unique tokens: ['adaptation', 'adjusts', 'allows', 'also', 'auxiliary']...)


In [11]:
# Create Corpus
texts = data
# Term Document Frequency and creating corpus
corpus = [id2word.doc2bow(text) for text in texts]

In [12]:
from gensim.models import ldaseqmodel
import numpy
from gensim.matutils import hellinger

In [13]:
time_slice = [2 , 1, 1, 99, 222, 257, 288, 290, 342, 360, 411, 403, 569, 679]

In [14]:
#ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus, id2word=id2word, time_slice=time_slice, num_topics=5)

ldaseq = ldaseqmodel.LdaSeqModel(corpus=corpus , id2word=id2word , num_topics=10, time_slice=time_slice)

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

...

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elogbeta[:, int(id)]) for id, cnt in doc)
C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldamodel.py:826: DeprecationWarning: Calling np.sum(generator) is deprecated, and in the future will give a different result. Use np.sum(np.fromiter(generator)) or the python sum builtin instead.
  score += np.sum(cnt * logsumexp(Elogthetad + Elog

C:\Users\Kornelius\Anaconda3\lib\site-packages\gensim\models\ldaseqmodel.py:230: RuntimeWarning: divide by zero encountered in double_scalars
  convergence = np.fabs((bound - old_bound) / old_bound)


In [15]:
ldaseq.print_topic_times(topic=0)# evolution of 1st topic through all timeslices

[[('network', 0.02333390604033782),
  ('system', 0.021552670135954674),
  ('model', 0.01578810805504332),
  ('time', 0.015462453975141191),
  ('dynamic', 0.01507607425290294),
  ('brain', 0.012255547702388216),
  ('activity', 0.01224000691324304),
  ('pattern', 0.009565543669668615),
  ('neural', 0.009513860351555714),
  ('state', 0.009512793978105435),
  ('data', 0.009475259382654474),
  ('memory', 0.008882131828959798),
  ('temporal', 0.007469106421312322),
  ('functional', 0.007200572951397122),
  ('user', 0.007025371387396787),
  ('series', 0.0058450994294342124),
  ('show', 0.00571037692868737),
  ('connectivity', 0.005580206884140239),
  ('dynamical', 0.0055380820986576105),
  ('event', 0.005457162149914069)],
 [('network', 0.02329851820151596),
  ('system', 0.021506610088315253),
  ('model', 0.015821484536929716),
  ('time', 0.015472277724746571),
  ('dynamic', 0.015131430122356041),
  ('brain', 0.012293767682216843),
  ('activity', 0.012278710901969964),
  ('pattern', 0.0095540

In [16]:
ldaseq.print_topic_times(topic=1)

[[('model', 0.05094572074472796),
  ('inference', 0.01732282068751578),
  ('data', 0.014198157573857019),
  ('distribution', 0.012919280341744362),
  ('method', 0.011968235772342623),
  ('bayesian', 0.011550246939676285),
  ('process', 0.011377658688654407),
  ('variable', 0.010180626188798147),
  ('latent', 0.009701870884695058),
  ('approach', 0.009074038729961596),
  ('structure', 0.008490945233350021),
  ('probabilistic', 0.007733674088592811),
  ('prior', 0.0066129929247146935),
  ('algorithm', 0.006521926219143905),
  ('using', 0.006503651057353327),
  ('gaussian', 0.00643860102702199),
  ('present', 0.005778030789011012),
  ('parameter', 0.0057057316310907425),
  ('show', 0.005630411287928029),
  ('variational', 0.005561781593443881)],
 [('model', 0.050946608065375466),
  ('inference', 0.017389060592520884),
  ('data', 0.014246568622732193),
  ('distribution', 0.012960554114568482),
  ('method', 0.012005027587303934),
  ('bayesian', 0.01158526428047471),
  ('process', 0.01137197

In [17]:
ldaseq.print_topic_times(topic=2)

[[('learning', 0.03030625199129462),
  ('method', 0.021150400654249515),
  ('data', 0.019305309532984465),
  ('feature', 0.016233325501726587),
  ('task', 0.012664417221176696),
  ('algorithm', 0.01126941838788064),
  ('approach', 0.011042560230048242),
  ('problem', 0.010956383310147342),
  ('kernel', 0.009730884507570942),
  ('classification', 0.008639855511299685),
  ('set', 0.0072578606081791334),
  ('show', 0.006903445688128539),
  ('label', 0.005965016709567284),
  ('proposed', 0.005880341605362567),
  ('paper', 0.005843080138426964),
  ('training', 0.005825124836918084),
  ('performance', 0.005769913469219889),
  ('using', 0.005598921141507316),
  ('large', 0.005287529403049816),
  ('propose', 0.005163362956621731)],
 [('learning', 0.030399322140203813),
  ('method', 0.021208762207209405),
  ('data', 0.019355645418893164),
  ('feature', 0.01627270662924029),
  ('task', 0.012691793413333015),
  ('algorithm', 0.011291904510178474),
  ('approach', 0.011065354550159289),
  ('problem

In [18]:
ldaseq.print_topic_times(topic=3)

[[('image', 0.04094472033673876),
  ('network', 0.021679618037668782),
  ('model', 0.020627172358574895),
  ('neural', 0.014117513795176428),
  ('deep', 0.012836939385651114),
  ('visual', 0.011986962568148053),
  ('layer', 0.010773314249839778),
  ('natural', 0.010568574118306752),
  ('architecture', 0.009437790603847862),
  ('field', 0.00811471833586793),
  ('feature', 0.007585171209517844),
  ('convolutional', 0.007533155242561803),
  ('input', 0.007529836317287142),
  ('representation', 0.006940754992204819),
  ('performance', 0.0068610566098197675),
  ('training', 0.006732501376133774),
  ('segmentation', 0.006522973319021444),
  ('show', 0.006436418941141135),
  ('result', 0.006053750236208012),
  ('weight', 0.005935573106942392)],
 [('image', 0.0409293135968133),
  ('network', 0.021552064358721708),
  ('model', 0.02071632817735564),
  ('neural', 0.014029259995969177),
  ('deep', 0.012894225822661455),
  ('visual', 0.01203790994886443),
  ('layer', 0.010816031347609186),
  ('natu

In [19]:
ldaseq.print_topic_times(topic=4)

[[('bound', 0.014886560338458654),
  ('function', 0.013652179458885059),
  ('regression', 0.01160948814875329),
  ('learning', 0.010365824137664154),
  ('distribution', 0.009966454534730204),
  ('loss', 0.009735451481962303),
  ('result', 0.00911268871791152),
  ('show', 0.00794139149178176),
  ('problem', 0.007932303922077907),
  ('algorithm', 0.007521661323136159),
  ('kernel', 0.007514704465721385),
  ('sample', 0.007512206120791509),
  ('error', 0.006749411734299174),
  ('estimation', 0.006445890414331371),
  ('data', 0.006407566680783138),
  ('estimator', 0.006395886885353883),
  ('rate', 0.006262613753825502),
  ('class', 0.006123293363697219),
  ('analysis', 0.005910130587142352),
  ('regularization', 0.005635795701650367)],
 [('bound', 0.014922300763460324),
  ('function', 0.013681752295594792),
  ('regression', 0.011634910101370579),
  ('learning', 0.010387009971196738),
  ('distribution', 0.00998633540529863),
  ('loss', 0.00975489220246363),
  ('result', 0.009130287270391169

In [20]:
ldaseq.print_topic_times(topic=5)

[[('algorithm', 0.039964497648509074),
  ('problem', 0.02981158705327493),
  ('method', 0.020392441991611002),
  ('function', 0.017635099009946198),
  ('optimization', 0.015131511243995074),
  ('gradient', 0.012306204763695705),
  ('convex', 0.011443841133338508),
  ('solution', 0.011073414850241535),
  ('convergence', 0.008980724133556581),
  ('show', 0.008512479592461037),
  ('approach', 0.007394935563712947),
  ('paper', 0.00687227107543984),
  ('learning', 0.006650241043539662),
  ('stochastic', 0.006604471213178348),
  ('approximation', 0.006129152523054225),
  ('descent', 0.005980467507113642),
  ('objective', 0.005935942738568839),
  ('result', 0.005423877870969743),
  ('linear', 0.005309459899401056),
  ('constraint', 0.005215778261245409)],
 [('algorithm', 0.04009187528398536),
  ('problem', 0.02989664891852636),
  ('method', 0.020444439160824952),
  ('function', 0.017677440503735525),
  ('optimization', 0.01516589008016045),
  ('gradient', 0.01233128448810125),
  ('convex', 0

In [21]:
ldaseq.print_topic_times(topic=6)

[[('neuron', 0.026819405595213553),
  ('spike', 0.017724892909906774),
  ('neural', 0.017225382475957483),
  ('information', 0.016619303204063973),
  ('response', 0.014366815991246671),
  ('stimulus', 0.014125268053373908),
  ('data', 0.01295309057924598),
  ('population', 0.012371384821777756),
  ('model', 0.009941409868681339),
  ('signal', 0.009779772634042847),
  ('input', 0.009136315130486211),
  ('mechanism', 0.009038202479689963),
  ('sensory', 0.008950570267131447),
  ('noise', 0.008230268212292032),
  ('rule', 0.00790810143224933),
  ('show', 0.007902102724390693),
  ('test', 0.007829527593451603),
  ('rate', 0.007819299452848117),
  ('correlation', 0.007747010832381805),
  ('spiking', 0.007371438693656757)],
 [('neuron', 0.026938683806535874),
  ('spike', 0.017783814421850154),
  ('neural', 0.017193470943707545),
  ('information', 0.016633617731699715),
  ('response', 0.014410233253680495),
  ('stimulus', 0.014166195675694632),
  ('data', 0.012988744510248623),
  ('population

In [22]:
ldaseq.print_topic_times(topic=7)

[[('model', 0.031611620562862174),
  ('object', 0.02409680850272999),
  ('image', 0.01794398682785827),
  ('human', 0.0151516001851632),
  ('task', 0.008590901890212678),
  ('approach', 0.00837812669586425),
  ('learning', 0.007370079144282284),
  ('recognition', 0.006832593404106011),
  ('training', 0.006741585071730551),
  ('data', 0.006412746069568022),
  ('motion', 0.006397504921352025),
  ('domain', 0.006278560098255672),
  ('visual', 0.005953722183145706),
  ('two', 0.0058510517391521895),
  ('using', 0.0058287632477241015),
  ('show', 0.005499904123564162),
  ('feature', 0.005457765128978116),
  ('detection', 0.00538024754601986),
  ('result', 0.00515680886962164),
  ('category', 0.005067601787432633)],
 [('model', 0.03176092219542536),
  ('object', 0.02413730669658824),
  ('image', 0.017961792701533686),
  ('human', 0.01522271088386109),
  ('task', 0.008617500608736197),
  ('approach', 0.00840362837756321),
  ('learning', 0.00737746113027385),
  ('recognition', 0.00685022846903

In [23]:
ldaseq.print_topic_times(topic=8)

[[('matrix', 0.026533921968605753),
  ('algorithm', 0.023840378180674617),
  ('clustering', 0.01971667598454885),
  ('graph', 0.01781523886049177),
  ('data', 0.017390451698123414),
  ('problem', 0.013688041787832901),
  ('sparse', 0.01329857105227718),
  ('method', 0.010827380023682831),
  ('show', 0.007853464686739624),
  ('number', 0.007776968380757461),
  ('analysis', 0.007749205434132616),
  ('cluster', 0.007371588307707811),
  ('result', 0.0066177938904848155),
  ('random', 0.006514438100396765),
  ('component', 0.006146009035647857),
  ('signal', 0.0058332494512565855),
  ('paper', 0.0049834801264436535),
  ('pca', 0.004836355726076072),
  ('using', 0.004769364619850312),
  ('subspace', 0.0046269848981178975)],
 [('matrix', 0.026639076245932498),
  ('algorithm', 0.02377196579305578),
  ('clustering', 0.01978264808043109),
  ('graph', 0.017872247223556407),
  ('data', 0.017443908831278283),
  ('problem', 0.013725737501363834),
  ('sparse', 0.013334849616930558),
  ('method', 0.01

In [24]:
ldaseq.print_topic_times(topic=9)

[[('algorithm', 0.031914826398290554),
  ('learning', 0.018953941333539323),
  ('problem', 0.01575303135457981),
  ('policy', 0.014341115777690277),
  ('online', 0.011123241162025732),
  ('show', 0.009393460082976085),
  ('regret', 0.008975297759234136),
  ('decision', 0.008800368807449582),
  ('action', 0.007956990795696284),
  ('state', 0.007650496657980094),
  ('bound', 0.0076251865307562635),
  ('optimal', 0.007401288513395179),
  ('reward', 0.006638759736026613),
  ('time', 0.006385171058763022),
  ('function', 0.006339147542563963),
  ('agent', 0.006068012083422434),
  ('game', 0.005947068047272581),
  ('setting', 0.005915247192607652),
  ('result', 0.005826607549233588),
  ('value', 0.005713854292079412)],
 [('algorithm', 0.0320159949418459),
  ('learning', 0.019002772319630185),
  ('problem', 0.01579180232602351),
  ('policy', 0.014375516373317446),
  ('online', 0.011146940925785323),
  ('show', 0.009410990445471865),
  ('regret', 0.0089925240267347),
  ('decision', 0.008816907

In [25]:

# to check Document - Topic proportions, use `doc-topics`
doc = ldaseq.doc_topics(558) # check the 558th document in the corpuses topic distribution
print (doc)
# this document is made up of different topics like this

[9.54523718e-02 6.19279056e-01 1.94791553e-01 2.12314225e-04
 2.12314225e-04 2.12314225e-04 8.92031346e-02 2.12314225e-04
 2.12314225e-04 2.12314225e-04]


In [26]:
# make a graph by checking the topic proportions and putting them on a graph 
# same with coherence
# do hellingers distance between topics?

In [27]:
ldaseq.print_topic_times(1) # evolution of values for all time slice for topic 2


[[('model', 0.05094572074472796),
  ('inference', 0.01732282068751578),
  ('data', 0.014198157573857019),
  ('distribution', 0.012919280341744362),
  ('method', 0.011968235772342623),
  ('bayesian', 0.011550246939676285),
  ('process', 0.011377658688654407),
  ('variable', 0.010180626188798147),
  ('latent', 0.009701870884695058),
  ('approach', 0.009074038729961596),
  ('structure', 0.008490945233350021),
  ('probabilistic', 0.007733674088592811),
  ('prior', 0.0066129929247146935),
  ('algorithm', 0.006521926219143905),
  ('using', 0.006503651057353327),
  ('gaussian', 0.00643860102702199),
  ('present', 0.005778030789011012),
  ('parameter', 0.0057057316310907425),
  ('show', 0.005630411287928029),
  ('variational', 0.005561781593443881)],
 [('model', 0.050946608065375466),
  ('inference', 0.017389060592520884),
  ('data', 0.014246568622732193),
  ('distribution', 0.012960554114568482),
  ('method', 0.012005027587303934),
  ('bayesian', 0.01158526428047471),
  ('process', 0.01137197

In [28]:
from gensim.models.coherencemodel import CoherenceModel

# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=2)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass1", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV1", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=3)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass2", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV2", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=4)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass3", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV3", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=5)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass4", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV4", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=6)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass5", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV5", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=7)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass6", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV6", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=8)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass7", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV7", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=9)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass8", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV8", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=10)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass9", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV9", cm_DTM.get_coherence())




# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=11)
# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass10", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV10", cm_DTM.get_coherence())


# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=12)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass11", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV11", cm_DTM.get_coherence())



# we just have to specify the time-slice we want to find coherence for.
topics_dtm = ldaseq.dtm_coherence(time=13)

# running u_mass coherence on our models
cm_DTM = CoherenceModel(topics=topics_dtm, corpus=corpus, dictionary=id2word, coherence='u_mass')

print ("U_Mass12", cm_DTM.get_coherence())

# to use 'c_v' we need texts, which we have saved to disk.
cm_DTM = CoherenceModel(topics=topics_dtm, texts=texts, dictionary=id2word, coherence='c_v')

print ("CV12", cm_DTM.get_coherence())

U_Mass1 -1.9438996081730333
CV1 0.43703622373526557
U_Mass2 -1.9434698318753412
CV2 0.43703622373526557
U_Mass3 -1.957143340591685
CV3 0.43880642092222066
U_Mass4 -1.9421238489601027
CV4 0.43703622373526557
U_Mass5 -1.9417265492502174
CV5 0.4375242653722178
U_Mass6 -1.9161481026924818
CV6 0.4331590763601936
U_Mass7 -1.9807562673748145
CV7 0.42420687246672417
U_Mass8 -1.959654314290987
CV8 0.42726507249366924
U_Mass9 -1.9391056903972803
CV9 0.430088842552551
U_Mass10 -1.923944578276225
CV10 0.4274704744351313
U_Mass11 -1.9408344537808877
CV11 0.426923707357576
U_Mass12 -1.959535942463404
CV12 0.42861305676432526


In [29]:
#https://datascience.blog.wzb.eu/2017/11/09/topic-modeling-evaluation-in-python-with-tmtoolkit/